# Sheet for extracting raw-data from Porto dataset


In [6]:
# Importing necessary modules

import pandas as pd
import os
import shutil
from haversine import haversine, Unit

# Helper function to compute distance between a list of coordinates (Trajectory distance)
# Haversine distance used


def calculate_trajectory_distance(positions: list[tuple[float]]) -> float:
    """
    Calculate the trajectory distance for a trajectory

    :param: List of coordinates (lat, lon)

    :return: Float (km) -> Combined distance between all pairs of points in km
    """
    distance = 0
    for i in range(1, len(positions)):
        from_location = positions[i - 1]
        to_location = positions[i]

        distance += haversine(from_location, to_location, unit=Unit.KILOMETERS)
    return distance

In [7]:
# Containning variables and constants for this spreadsheet
SHOULD_DELETE_OLD_FILES = False

OUTPUT_FOLDER = "../dataset/porto/output/"
RAW_DATA_FILE = "../dataset/porto/porto_raw.csv"
CLEAN_DATA_FILE = "../dataset/porto/porto.csv"

LOG = False  # Set to true for printing during data extraction

MAX_LON = -8.57
MIN_LON = -8.66
MAX_LAT = 41.19
MIN_LAT = 41.14
MIN_LEN = 40

NUMBER_OF_TRACES = 3000
MAX_DIST_BETWEEN_COORDINATES = 0.2  # Km

X = calculate_trajectory_distance([(MIN_LAT, MIN_LON), (MAX_LAT, MIN_LON)])
Y = calculate_trajectory_distance([(MIN_LAT, MIN_LON), (MIN_LAT, MAX_LON)])

In [8]:
# Reading the dataset into dataframe

raw_df = pd.read_csv(RAW_DATA_FILE)

In [9]:
# Run this cell to clear the chosen files in the PORTO folder

if SHOULD_DELETE_OLD_FILES:
    for filename in os.listdir(OUTPUT_FOLDER):
        file_path = os.path.join(OUTPUT_FOLDER, filename)
        try:
            if os.path.isfile(file_path) or os.path.islink(file_path):
                os.unlink(file_path)
            elif os.path.isdir(file_path):
                shutil.rmtree(file_path)
        except Exception as e:
            print("Failed to remove %s. Reason: %s" % (file_path, e))

In [10]:
# Read the data, clean it and insert to cleaned csv file

from utils.alphabetical import increment_alphabetical
from utils.save_trajectory import save_current_trajectory


cleaned_trajectories = []
counter = 0
name_counter = "AAA"

for index, row in raw_df.iterrows():
    trace_id = row["TRIP_ID"]

    # If row is missing data: ignore row
    if row["MISSING_DATA"] == True:
        if LOG:
            print(trace_id, "is missing data")
        continue

    trace = row["POLYLINE"][2:-2].split("],[")

    # If trace-length less than "MIN_LEN": ignore row
    if len(trace) < MIN_LEN:
        if LOG:
            print(trace_id, "is less than preferred length")
        continue

    # If trace are outside bounded rectangle or noisy data: ignore row

    last_coordinate = trace[0]
    for coordinate in trace:
        lon, lat = list(map(float, coordinate.split(",")))

        # Outside bounded rectangle
        if (not (MIN_LAT <= lat <= MAX_LAT)) or (not (MIN_LON <= lon <= MAX_LON)):
            if LOG:
                print(trace_id, "is outside bounded rectangle")
            break

        # Traces with noisy data:
        if last_coordinate != coordinate:
            last_lon, last_lat = list(map(float, last_coordinate.split(",")))
            distance = calculate_trajectory_distance([(last_lat, last_lon), (lat, lon)])

            # If distance between two consecutive coordinates are too great:
            if distance > MAX_DIST_BETWEEN_COORDINATES:
                if LOG:
                    print("Possibly noisy data - continuing with next trace")
                break

        last_coordinate = coordinate
        # IMPLEMENT HERE, use distance function

    # Else, everything is good so far --> Write trajectory to file
    else:
        cleaned_trajectories.append(row)
        save_current_trajectory(
            OUTPUT_FOLDER=OUTPUT_FOLDER,
            file_name=name_counter,
            trajectory=trace,
            split_coordinate=True,
        )

        counter += 1
        name_counter = increment_alphabetical(name_counter)

        if counter >= NUMBER_OF_TRACES:
            break

cleaned_df_columns = [
    "TRIP_ID",
    "CALL_TYPE",
    "ORIGIN_CALL",
    "ORIGIN_STAND",
    "TAXI_ID",
    "TIMESTAMP",
    "DAY_TYPE",
    "MISSING_DATA",
    "POLYLINE",
]
cleaned_df = pd.DataFrame(cleaned_trajectories, columns=cleaned_df_columns)
cleaned_df.to_csv(CLEAN_DATA_FILE, index=False)


print("Number of cleaned trajectories written to file:", counter)

['-8.616033,41.140485', '-8.614755,41.140944', '-8.614404,41.141925', '-8.61381,41.143032', '-8.612523,41.144013', '-8.611965,41.144481', '-8.611794,41.144553', '-8.611695,41.144553', '-8.611182,41.144958', '-8.610534,41.143995', '-8.60931,41.143203', '-8.6085,41.143113', '-8.6085,41.143122', '-8.608482,41.143122', '-8.607375,41.14251', '-8.605341,41.142987', '-8.604621,41.143914', '-8.60301,41.14341', '-8.602713,41.143347', '-8.602713,41.143356', '-8.602713,41.143347', '-8.602722,41.143338', '-8.602749,41.14332', '-8.602767,41.143302', '-8.602749,41.143311', '-8.602749,41.143311', '-8.602749,41.143329', '-8.602749,41.143356', '-8.602758,41.143356', '-8.602758,41.143365', '-8.602308,41.143194', '-8.602281,41.143644', '-8.602875,41.144733', '-8.602884,41.144796', '-8.602884,41.144814', '-8.603163,41.145417', '-8.601858,41.145831', '-8.602101,41.146929', '-8.603046,41.146632', '-8.604828,41.146614', '-8.606259,41.146884', '-8.607672,41.147217', '-8.608077,41.147406', '-8.607699,41.147901

In [ ]:
from utils.metafile_handler import create_meta_files, get_meta_files, delete_meta_files

create_meta_files(path_to_files=OUTPUT_FOLDER,
                  data_prefix="R_", create_test_set=True)